In [17]:
""" 
    RNA Alignment Assignment
    
    Implement each of the functions below using the algorithms covered in class.
    You can construct additional functions and data structures but you should not
    change the functions' APIs.

    You will be graded on the helper function implementations as well as the RNA alignment, although
    you do not have to use your helper function.
    
    *** Make sure to comment out any print statement so as not to interfere with the grading script
"""

import sys # DO NOT EDIT THIS
from shared import *

ALPHABET = [TERMINATOR] + BASES

def get_suffix_array(s):
    """
    Naive implementation of suffix array generation (0-indexed). You do not have to implement the
    KS Algorithm. Make this code fast enough so you have enough time in Aligner.__init__ (see bottom).

    Input:
        s: a string of the alphabet ['A', 'C', 'G', 'T'] already terminated by a unique delimiter '$'
    
    Output: list of indices representing the suffix array

    >>> get_suffix_array('GATAGACA$')
    [8, 7, 5, 3, 1, 6, 4, 0, 2]
    """
    buckets = {}
    for i in range(len(s)):
        if s[i:i+100] in buckets:
            buckets[s[i:i+100]].append(i)
        else:
            buckets[s[i:i+100]] = [i]
    
    for item in buckets:
        if len(buckets[item]) > 1:
            # needs additional sorting
            buckets[item].sort(key=lambda index: s[index:])
    
    sorted_bucket_keys = sorted(buckets.keys())
    result = []
    for item in sorted_bucket_keys:
        result.extend(buckets[item])
    
    return result

def get_bwt(s, sa):
    """
    Input:
        s: a string terminated by a unique delimiter '$'
        sa: the suffix array of s

    Output:
        L: BWT of s as a string
    """
    return ''.join([s[i-1] for i in sa])

def get_F(L):
    """
    Input: L = get_bwt(s)

    Output: F, first column in Pi_sorted
    """
    return ''.join(sorted(list(L)))

def get_M(F):
    """
    Returns the helper data structure M (using the notation from class). M is a dictionary that maps character
    strings to start indices. i.e. M[c] is the first occurrence of "c" in F.

    If a character "c" does not exist in F, you may set M[c] = -1
    """
    M = {}
    for i in range(len(F)):
        char = F[i]
        if char not in M:
            M[char] = i
    for char in ALPHABET:
        if char not in M:
            M[char] = -1
    return M

def get_occ(L):
    """
    Returns the helper data structure OCC (using the notation from class). OCC should be a dictionary that maps 
    string character to a list of integers. If c is a string character and i is an integer, then OCC[c][i] gives
    the number of occurrences of character "c" in the bwt string up to and including index i
    """
    occ = {i: [0] for i in ALPHABET}
    for i in L:
        for j in occ:
            if i != j:
                occ[j].append(occ[j][-1])
            else:
                occ[i].append(occ[i][-1]+1)
    for i in occ:
        occ[i].pop(0)
    return occ

def construct_L(M, occ):
    length = 0
    for char in occ:
        length += occ[char][-1]
    L = ['']*length
    for char in occ:
        for i in range(occ[char][-1]):
            L[occ[char].index(i+1)] = char
    return ''.join(L)
    
def exact_suffix_matches(p, M, occ):
    """
    Find the positions within the suffix array sa of the longest possible suffix of p 
    that is a substring of s (the original string).
    
    Note that such positions must be consecutive, so we want the range of positions.

    Input:
        p: the pattern string
        M, occ: buckets and repeats information used by sp, ep

    Output: a tuple (range, length)
        range: a tuple (start inclusive, end exclusive) of the indices in sa that contains
            the longest suffix of p as a prefix. range=None if no indices matches any suffix of p
        length: length of the longest suffix of p found in s. length=0 if no indices matches any suffix of p

        An example return value would be ((2, 5), 7). This means that p[len(p) - 7 : len(p)] is
        found in s and matches positions 2, 3, and 4 in the suffix array.

    >>> s = 'ACGT' * 10 + '$'
    >>> sa = get_suffix_array(s)
    >>> sa
    [40, 36, 32, 28, 24, 20, 16, 12, 8, 4, 0, 37, 33, 29, 25, 21, 17, 13, 9, 5, 1, 38, 34, 30, 26, 22, 18, 14, 10, 6, 2, 39, 35, 31, 27, 23, 19, 15, 11, 7, 3]
    >>> L = get_bwt(s, sa)
    >>> L
    'TTTTTTTTTT$AAAAAAAAAACCCCCCCCCCGGGGGGGGGG'
    >>> F = get_F(L)
    >>> F
    '$AAAAAAAAAACCCCCCCCCCGGGGGGGGGGTTTTTTTTTT'
    >>> M = get_M(F)
    >>> sorted(M.items())
    [('$', 0), ('A', 1), ('C', 11), ('G', 21), ('T', 31)]
    >>> occ = get_occ(L)
    >>> type(occ) == dict, type(occ['$']) == list, type(occ['$'][0]) == int
    (True, True, True)
    >>> occ['$']
    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
    >>> exact_suffix_matches('ACTGA', M, occ)
    ((1, 11), 1)
    >>> exact_suffix_matches('$', M, occ)
    ((0, 1), 1)
    >>> exact_suffix_matches('AA', M, occ)
    ((1, 11), 1)
    """
    
    # initialize sp, ep
    length = len(p)
    last_char = p[-1]
    sp = M[last_char]
    if sp == -1:
        return (None, 0)
    
    # find next(last_char)
    nxt = float('inf')
    nxt_item = None
    for item in M:
        if nxt > M[item] > M[last_char] and item != last_char:
            nxt = M[item]
            nxt_item = item
    if nxt_item == None:
        ep = len(occ['$']) - 1
    else:
        ep = nxt - 1
    
    # changed for loop a bit, only works on strings len >= 2
    # for strings of len 1, it skips to the end and works
    for i in range(length-2,-1,-1):
        sp_ph = M[p[i]] + occ[p[i]][sp-1]
        ep_ph = M[p[i]] + occ[p[i]][ep]-1
        if sp_ph > ep_ph:
            return ((sp,ep+1),length-i-1)
        sp = sp_ph
        ep = ep_ph
    return ((sp,ep+1), length)

MIN_INTRON_SIZE = 20
MAX_INTRON_SIZE = 10000

class Aligner: 
    def __init__(self, genome_sequence, known_genes):
        """
        Initializes the aligner. Do all time intensive set up here. i.e. build suffix array.

        genome_sequence: a string (NOT TERMINATED BY '$') representing the bases of the of the genome
        known_genes: a python set of Gene objects (see shared.py) that represent known genes. You can get the isoforms 
                     and exons from a Gene object

        Time limit: 500 seconds maximum on the provided data. Note that our server is probably faster than your machine, 
                    so don't stress if you are close. Server is 1.25 times faster than the i7 CPU on my computer

        """
        self.genome_sa = get_suffix_array(genome_sequence)
        self.genome_L = get_bwt(genome_sequence, self.genome_sa)
        self.genome_M = get_M(get_F(self.genome_L))
        self.genome_occ = get_occ(self.genome_L)

    def align(self, read_sequence):
        """
        Returns an alignment to the genome sequence. An alignment is a list of pieces. 
        Each piece consists of a start index in the read, a start index in the genome, and a length 
        indicating how many bases are aligned in this piece. Note that mismatches are count as "aligned".

        Note that <read_start_2> >= <read_start_1> + <length_1>. If your algorithm produces an alignment that 
        violates this, we will remove pieces from your alignment arbitrarily until consecutive pieces 
        satisfy <read_start_2> >= <read_start_1> + <length_1>

        Return value must be in the form (also see the project pdf):
        [(<read_start_1>, <reference_start_1, length_1), (<read_start_2>, <reference_start_2, length_2), ...]

        If no good matches are found: return the best match you can find or return []

        Time limit: 0.5 seconds per read on average on the provided data.
        """
        pass

In [18]:
with open('bases.txt') as f:
    a = Aligner(f.read().strip(), [])

a.genome_sa

[5000000,
 4992108,
 2619790,
 4107518,
 1956968,
 4992109,
 2733738,
 243139,
 4371684,
 2685341,
 1462284,
 868453,
 2455967,
 2619791,
 2580545,
 1884336,
 4663864,
 2245386,
 4257254,
 3586127,
 4776048,
 711169,
 3530524,
 1142878,
 3104321,
 3476303,
 3661584,
 4107519,
 402618,
 3206879,
 2260164,
 1956969,
 1847169,
 277045,
 4750019,
 4992110,
 4927669,
 2733739,
 2847074,
 4784152,
 243140,
 128064,
 2143013,
 4371685,
 4671492,
 2685342,
 4016325,
 4848025,
 4595171,
 3248215,
 1965331,
 1462285,
 1349972,
 771206,
 3685091,
 868454,
 4228260,
 2455968,
 2619792,
 2580546,
 3223997,
 1884337,
 4421378,
 2034505,
 2833649,
 2146450,
 4396489,
 2843011,
 4663865,
 2245387,
 4257255,
 3586128,
 4776049,
 4057962,
 711170,
 3724881,
 4935849,
 3005160,
 3017221,
 3129539,
 277804,
 3609169,
 6220,
 4598098,
 756028,
 3530525,
 2734251,
 630410,
 2361624,
 1142879,
 3881323,
 2388512,
 2703668,
 3104322,
 3476304,
 1939011,
 3661585,
 2301432,
 4254164,
 14597,
 4172170,
 3524402

In [19]:
a.genome_L

'...'